<a href="https://colab.research.google.com/github/FranceCosta/Isopeptor_development/blob/main/notebooks/Isopeptide_finder.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%%capture

# @markdown # Install dependencies

!pip install isopeptor
!pip install py3Dmol
!pip install Bio

import os
import glob
import requests
from pathlib import Path
from Bio.PDB.PDBList import PDBList
from isopeptor.isopeptide import Isopeptide
import py3Dmol
from IPython.display import display, HTML

def downloadAF2(uniprot_acc: str, outdir: str, version='v4') -> bool:
    """

        Download AlphaFold models from the AlphaFold database and parse them to
        keep the structure of the desired seqeunce.

        PARAMETERS
        ----------
        auniprot_acc:str,  Uniprot accession code;
        outdir: str, path to directory where to save PDB structure;
        version: str, alphafold database version (default: v4);

        RETURNS
        bool: False if no structure or a wrong structure has been obtained;

    """

    download_link = "https://alphafold.ebi.ac.uk/files/AF-{}-F1-model_{}.pdb"
    output = os.path.join(outdir, f'{uniprot_acc}.pdb')

    try:
        r = requests.get(
            download_link.format(uniprot_acc, version))
        r.raise_for_status()

    except requests.exceptions.HTTPError as e:
        print(f"During download from the AFDB the")
        print(f"following error occurred:\n{e}")
        return 0

    open(output, 'wb').write(r.content)

    return 1

In [2]:
# @markdown #Parameters

# @markdown Read the full documentation [here](https://isopeptor.readthedocs.io/en/latest/index.html).

# @markdown Insert PDB code, AFDB code or path (example: 1amx, A0A061LY60, your_protein.pdb)
structure_name = "A0A061LY60" #@param {type:"string"}
# @markdown Higher distance values allow a more permessive search
distance = 1.5 #@param {type:"slider", min:0.5, max:5, step:0.5}
# @markdown Fix asa to 0.1 for a quicker computation
fixed_asa = False #@param {type:"boolean"}
if fixed_asa:
    fixed_asa_value = 0.1
# @markdown Evaluate geometric parameters of isopeptide bonds.
# @markdown If set True, geometric data will be included in the output table.
geometry_evaluation = False #@param {type:"boolean"}

In [3]:
# @markdown #Run

os.makedirs("structures", exist_ok=True)
print("Removing pre-existing structures")
files = glob.glob("structures/*")
for f in files:
    os.remove(f)
# Download structure if not a path
if not os.path.isfile(structure_name):
    if len(structure_name) > 4:
        print(f"Downloading AFDB structure {structure_name}...")
        download_status = downloadAF2(structure_name, "./structures")
        assert download_status == True, "Download from AFDB failed"
        new_structure_name = os.path.join("structures", f"{structure_name}.pdb")

    elif len(structure_name) == 4:
        pdbl = PDBList()
        pdb_filename = pdbl.retrieve_pdb_file(structure_name, file_format="pdb",
                                              pdir="./structures", overwrite=True)
        new_structure_name = os.path.join("structures", f"{structure_name}.pdb")
        os.rename(pdb_filename, new_structure_name)

    else:
        print("Structure should be a PDB code, AFDB code or path: none of this found.")
else:
    print("Moving structure to structures folder.")
    os.rename(structure_name, os.path.join("structures", os.path.basename(structure_name)))
    new_structure_name = os.path.join("structures", os.path.basename(structure_name))

structure_path = os.path.dirname(new_structure_name)

# Run isopeptor
print("Running isopeptor...")
if fixed_asa:
    i = Isopeptide(structure_path, distance=distance, fixed_r_asa=fixed_asa_value)
else:
    i = Isopeptide(structure_path, distance=distance)
i.predict()
if geometry_evaluation:
    i.get_geometry()
print("Isopeptor run ok.")

Removing pre-existing structures
Running isopeptor...
Isopeptor run ok.


/usr/local/lib/python3.11/dist-packages/sklearn/base.py:380: InconsistentVersionWarning: Trying to unpickle estimator LogisticRegression from version 1.3.0 when using version 1.6.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(


In [4]:
# @markdown Show results
i.print_tabular()

# Function to create a flexible grid layout
def create_viewer_grid(num_columns, num_rows, main_width=800, bond_width=400, height=400):
    grid_html = '<table style="width:100%; table-layout:fixed;">'
    grid_html += '<tr>'  # Start the row
    grid_html += f'<td id="viewer_0" style="width:{main_width}px; height:{height}px;"></td>'
    for i in range(1, num_columns):
        grid_html += f'<td id="viewer_{i}" style="width:{bond_width}px; height:{height}px;"></td>'
    grid_html += '</tr></table>'
    display(HTML(grid_html))
    return [f'viewer_{i}' for i in range(num_columns)]

# Load the protein structure
with open(new_structure_name, 'r') as file:
    pdb_data = file.read()

# Number of isopeptide bonds
num_isopeptide_bonds = len(i.isopeptide_bonds)

# Create a grid where the first column (main view) is wider than the others
viewer_ids = create_viewer_grid(num_columns=num_isopeptide_bonds + 1, num_rows=1)

# Initialize the main protein view (wider than others)
main_view = py3Dmol.view(width=800, height=400, js='https://3dmol.csb.pitt.edu/build/3Dmol.js')
main_view.addModel(pdb_data, 'pdb')
main_view.setStyle({'cartoon': {'color': 'gray'}})

# Add styles for isopeptide bonds in the main view
for bond in sorted(i.isopeptide_bonds, key=lambda x: x.probability):
    chain = bond.chain
    match_residues = (bond.r1_bond, bond.r_cat, bond.r2_bond)
    prob = bond.probability
    color = 'greenCarbon' if prob > 0.5 else 'grayCarbon'
    main_view.addStyle({'chain': chain, 'resi': match_residues}, {'stick': {'colorscheme': color}})

main_view.zoomTo()
main_view.show()

# Create zoomed-in views for each isopeptide bond
for idx, bond in enumerate(sorted(i.isopeptide_bonds, key=lambda x: x.probability)):
    zoom_view = py3Dmol.view(width=400, height=400, js='https://3dmol.csb.pitt.edu/build/3Dmol.js')
    zoom_view.addModel(pdb_data, 'pdb')
    chain = bond.chain
    match_residues = (bond.r1_bond, bond.r_cat, bond.r2_bond)
    prob = bond.probability
    color = 'greenCarbon' if prob > 0.5 else 'grayCarbon'
    zoom_view.setStyle({'chain': chain, 'resi': match_residues}, {'stick': {'colorscheme': color}})
    zoom_view.zoomTo({'chain': chain, 'resi': match_residues})
    zoom_view.show()


protein_name	probability	chain	r1_bond	r_cat	r2_bond	r1_bond_name	r_cat_name	r2_bond_name	bond_type	rmsd 	r_asa	template             
A0A061LY60  	0.896      	A    	719    	756  	821    	LYS         	ASP       	ASN         	CnaA-like	0.352	0.027	2f68_X_176_209_293   
A0A061LY60  	0.88       	A    	566    	603  	668    	LYS         	ASP       	ASN         	CnaA-like	0.37 	0.042	2f68_X_176_209_293   
A0A061LY60  	0.856      	A    	425    	462  	534    	LYS         	ASP       	ASN         	CnaA-like	0.397	0.047	2wza_A_1082_1132_1232


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [5]:
# @markdown Download results table
from google.colab import files
i.save_csv()
files.download("results.csv")


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>